In [1]:
import utils
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import OneHotEncoder, StandardScaler
from xgboost import XGBRegressor
from sklearn.pipeline import Pipeline
from scipy.sparse import hstack
from xgboost import XGBRegressor
import pandas as pd
import numpy as np
from skrub import TableReport
from jours_feries_france import JoursFeries
from vacances_scolaires_france import SchoolHolidayDates

In [2]:
data = pd.read_parquet("data/train.parquet")
# Sort by date first, so that time based cross-validation would produce correct results
data = data.sort_values(["date", "counter_name"])
# y_train = data['log_bike_count'].values
# X_train = data.drop(['log_bike_count', "bike_count"], axis=1)

In [3]:
data

counter_id                       counter_name    site_id  \
400125  100049407-353255860  152 boulevard du Montparnasse E-O  100049407   
408305  100049407-353255859  152 boulevard du Montparnasse O-E  100049407   
87516   100036719-104036719  18 quai de l'Hôtel de Ville NO-SE  100036719   
98518   100036719-103036719  18 quai de l'Hôtel de Ville SE-NO  100036719   
875137  100063175-353277233          20 Avenue de Clichy NO-SE  100063175   
...                     ...                                ...        ...   
792857  100057329-103057329   Totem 85 quai d'Austerlitz SE-NO  100057329   
805182  100057380-104057380           Totem Cours la Reine E-O  100057380   
815218  100057380-103057380           Totem Cours la Reine O-E  100057380   
125979  100042374-110042374        Voie Georges Pompidou NE-SO  100042374   
135985  100042374-109042374        Voie Georges Pompidou SO-NE  100042374   

                            site_name  bike_count                date  \
400125  152 boulevard du Montparnasse         4.0 2020-09-01 01:00:00   
408305  152 boulevard du Montparnasse         3.0 2020-09-01 01:00:00   
87516     18 quai de l'Hôtel de Ville         0.0 2020-09-01 01:00:00   
98518     18 quai de l'Hôtel de Ville         1.0 2020-09-01 01:00:00   
875137            20 Avenue de Clichy         7.0 2020-09-01 01:00:00   
...                               ...         ...                 ...   
792857     Totem 85 quai d'Austerlitz        42.0 2021-09-09 23:00:00   
805182           Totem Cours la Reine        22.0 2021-09-09 23:00:00   
815218           Totem Cours la Reine        32.0 2021-09-09 23:00:00   
125979          Voie Georges Pompidou         9.0 2021-09-09 23:00:00   
135985          Voie Georges Pompidou         7.0 2021-09-09 23:00:00   

       counter_installation_date         coordinates counter_technical_id  \
400125                2018-12-07  48.840801,2.333233          Y2H19070373   
408305                2018-12-07  48.840801,2.333233          Y2H19070373   
87516                 2017-07-12    48.85372,2.35702          Y2H19027732   
98518                 2017-07-12    48.85372,2.35702          Y2H19027732   
875137                2020-07-22    48.88529,2.32666          Y2H20073268   
...                          ...                 ...                  ...   
792857                2020-02-18    48.84201,2.36729          YTH19111508   
805182                2020-02-11    48.86462,2.31444          YTH19111509   
815218                2020-02-11    48.86462,2.31444          YTH19111509   
125979                2017-12-15     48.8484,2.27586          Y2H21025335   
135985                2017-12-15     48.8484,2.27586          Y2H21025335   

         latitude  longitude  log_bike_count  
400125  48.840801   2.333233        1.609438  
408305  48.840801   2.333233        1.386294  
87516   48.853720   2.357020        0.000000  
98518   48.853720   2.357020        0.693147  
875137  48.885290   2.326660        2.079442  
...           ...        ...             ...  
792857  48.842010   2.367290        3.761200  
805182  48.864620   2.314440        3.135494  
815218  48.864620   2.314440        3.496508  
125979  48.848400   2.275860        2.302585  
135985  48.848400   2.275860        2.079442  

[496827 rows x 12 columns]

In [4]:
external_conditions = pd.read_csv('data/external_data.csv')
external_conditions['date'] = pd.to_datetime(external_conditions['date'])
external_conditions

numer_sta                date    pmer  tend  cod_tend   dd   ff       t  \
0          7149 2021-01-01 00:00:00  100810    80         1  270  1.8  272.75   
1          7149 2021-01-01 03:00:00  100920   110         3  300  1.7  271.25   
2          7149 2021-01-01 06:00:00  100950    30         3  290  2.6  271.95   
3          7149 2021-01-01 09:00:00  101100   150         2  280  1.7  272.45   
4          7149 2021-01-01 12:00:00  101110    30         0   50  1.0  276.95   
...         ...                 ...     ...   ...       ...  ...  ...     ...   
3317       7149 2020-09-30 09:00:00  101540   -30         8  230  4.4  289.95   
3318       7149 2020-09-30 12:00:00  101320  -210         8  190  4.9  292.05   
3319       7149 2020-09-30 15:00:00  101140  -180         7  190  4.1  291.55   
3320       7149 2020-09-30 18:00:00  101020  -130         6  190  2.7  290.15   
3321       7149 2020-09-30 21:00:00  100880  -140         8  170  2.4  288.35   

          td   u  ...  hnuage1  nnuage2  ctype2  hnuage2  nnuage3  ctype3  \
0     272.15  96  ...    600.0      NaN     NaN      NaN      NaN     NaN   
1     270.95  98  ...   1500.0      2.0     3.0   3000.0      NaN     NaN   
2     271.65  98  ...    480.0      4.0     6.0   2000.0      6.0     3.0   
3     272.05  97  ...   1740.0      3.0     3.0   2800.0      NaN     NaN   
4     274.15  82  ...    330.0      4.0     6.0    570.0      7.0     6.0   
...      ...  ..  ...      ...      ...     ...      ...      ...     ...   
3317  286.85  82  ...    400.0      7.0     6.0   2200.0      NaN     NaN   
3318  285.55  66  ...    870.0      7.0     6.0   1900.0      NaN     NaN   
3319  286.45  72  ...    820.0      7.0     6.0   2200.0      NaN     NaN   
3320  285.25  73  ...   2160.0      NaN     NaN      NaN      NaN     NaN   
3321  285.85  85  ...   1980.0      7.0     0.0   5700.0      NaN     NaN   

      hnuage3  nnuage4  ctype4  hnuage4  
0         NaN      NaN     NaN      NaN  
1         NaN      NaN     NaN      NaN  
2      3000.0      NaN     NaN      NaN  
3         NaN      NaN     NaN      NaN  
4       810.0      NaN     NaN      NaN  
...       ...      ...     ...      ...  
3317      NaN      NaN     NaN      NaN  
3318      NaN      NaN     NaN      NaN  
3319      NaN      NaN     NaN      NaN  
3320      NaN      NaN     NaN      NaN  
3321      NaN      NaN     NaN      NaN  

[3322 rows x 59 columns]

In [5]:
# Drop columns with more than 40% NaN values
threshold = len(external_conditions) * 0.4
external_conditions = external_conditions.dropna(thresh=threshold, axis=1)

In [7]:
merged_conditions = data.merge(external_conditions, on='date', how='left')
TableReport(merged_conditions)

Processing column  51 / 51


<TableReport: use .open() to display>

In [ ]:
# # Step 1: Sort the `external_conditions` DataFrame by the `date` column
# external_conditions = external_conditions.sort_values(by='date')

# # Drop columns with more than 40% NaN values
# threshold = len(external_conditions) * 0.4
# external_conditions = external_conditions.dropna(thresh=threshold, axis=1)

# # Step 2: Remove duplicate entries based on the `date` column
# external_conditions = external_conditions.drop_duplicates(subset='date')

# # Step 3: Convert the 'date' column to datetime
# external_conditions['date'] = pd.to_datetime(external_conditions['date'])

# # Step 4: Create a complete date range from the minimum to the maximum date in the DataFrame
# date_range = pd.date_range(start=external_conditions['date'].min(), end=external_conditions['date'].max(), freq='H')

# # Step 5: Create a DataFrame from the date_range
# date_range_df = pd.DataFrame(date_range, columns=['date'])

# # Step 6: Merge the date_range DataFrame with the external_conditions DataFrame on the 'date' column
# full_external_conditions = pd.merge(date_range_df, external_conditions, on='date', how='left')

# # Fonction qui fait ce qu'on voulait faire avec ffill et bfill mais a la place prends la valeur la plus proche
# def fill_closest_value_all_columns(df):
#     """Fill NaN values with the closest value for all numeric columns in the DataFrame."""
#     filled_df = df.copy()
    
#     for column in filled_df.columns:
#         if filled_df[column].dtype.kind in 'biufc':  # Numeric columns
#             non_nan_values = filled_df[column].dropna()
            
#             def find_closest(value):
#                 if pd.isna(value):
#                     closest_value = non_nan_values.iloc[(non_nan_values - value).abs().argmin()]
#                     return closest_value
#                 return value
            
#             filled_df[column] = filled_df[column].apply(find_closest)
    
#     return filled_df

# # Apply the function to the DataFrame
# filled_external_conditions = fill_closest_value_all_columns(full_external_conditions)

In [ ]:
# # Ensure 'date' column in external_conditions is of datetime type
# # filled_external_conditions['date'] = pd.to_datetime(filled_external_conditions['date'])

# # Merge the DataFrames
# merged_conditions = pd.merge(X_train, filled_external_conditions, on='date', how='left')

# merged_conditions = utils._column_rename(merged_conditions)

In [12]:
# Ensure "date" is in datetime format
merged_conditions = utils._column_rename(merged_conditions)
merged_conditions["date"] = pd.to_datetime(merged_conditions["date"], errors="coerce")

# Drop rows with invalid datetime entries
df = merged_conditions.dropna(subset=["date"])

# Extract date and time features
df["year"] = df["date"].dt.year
df["month"] = df["date"].dt.month
df["weekday"] = df["date"].dt.dayofweek
df["day"] = df["date"].dt.day
df["hour"] = df["date"].dt.hour
df["is_weekend"] = (df["weekday"] >= 5).astype(int)

# Handle school and public holidays
unique_dates = df["date"].dt.date.unique()
d = SchoolHolidayDates()
f = JoursFeries()

try:
    dict_school_holidays = {date: d.is_holiday_for_zone(date, "C") for date in unique_dates}
    df["is_school_holiday"] = df["date"].dt.date.map(dict_school_holidays).fillna(0).astype(int)
except Exception as e:
    print(f"Error with school holidays mapping: {e}")
    df["is_school_holiday"] = 0

try:
    dict_public_holidays = {date: f.is_bank_holiday(date, zone="Métropole") for date in unique_dates}
    df["is_public_holiday"] = df["date"].dt.date.map(dict_public_holidays).fillna(0).astype(int)
except Exception as e:
    print(f"Error with public holidays mapping: {e}")
    df["is_public_holiday"] = 0

In [13]:
TableReport(df)

Processing column  59 / 59


<TableReport: use .open() to display>

In [15]:
# Add the new category to categorical columns
for col in df.select_dtypes(include=['category']).columns:
	df[col] = df[col].cat.add_categories([0])

# Fill NaN values with 0
df = df.fillna(0)

In [ ]:
y_train = df['log_bike_count'].values
X_train = df.drop(['log_bike_count', "bike_count"], axis=1)

date_cols = ["year", "month", "weekday", "day", "hour", "is_weekend", "is_school_holiday", "is_public_holiday"]
categorical_cols = ["counter_name"]
numerical_cols = [
    'latitude', 'longitude', 'Sea Level Pressure (hPa)', 'Pressure Tendency (hPa/3h)',
    'Pressure Tendency Code', 'Wind Direction (°)', 'Wind Speed (m/s)', 'Air Temperature (°C)',
    'Dew Point Temperature (°C)', 'Relative Humidity (%)', 'Visibility (m)', 'Present Weather Code',
    'Past Weather Code 1', 'Past Weather Code 2', 'Total Cloud Cover (oktas)', 'Cloud Base Height (m)',
    'Lowest Cloud Base Height (m)', 'Low Cloud Type', 'Station Level Pressure (hPa)', '24h Pressure Tendency (hPa)',
    '10min Max Wind Gust (m/s)', 'Max Wind Gust (m/s)', 'Measurement Period Duration', 'Ground State',
    'Snow Height (cm)', 'New Snow Depth (cm)', 'New Snowfall Duration (hours)', 'Rainfall (1h, mm)',
    'Rainfall (3h, mm)', 'Rainfall (6h, mm)', 'Rainfall (12h, mm)', 'Rainfall (24h, mm)',
    'Layer 1 Cloud Cover (oktas)', 'Layer 1 Cloud Type', 'Layer 1 Cloud Base Height (m)'
]


# 1. Apply column transformations
# One-hot encode date columns
date_encoder = OneHotEncoder(handle_unknown="ignore")
date_encoded = date_encoder.fit_transform(X_train[date_cols])

# One-hot encode categorical columns
cat_encoder = OneHotEncoder(handle_unknown="ignore")
cat_encoded = cat_encoder.fit_transform(X_train[categorical_cols])

# Standard scale numerical columns
num_scaler = StandardScaler()
num_scaled = num_scaler.fit_transform(X_train[numerical_cols])

X_transformed = hstack([date_encoded, cat_encoded, num_scaled]).toarray()

# 2. Train the model
model = XGBRegressor(
    objective='reg:squarederror',
    n_estimators=100,
    learning_rate=0.1,
    max_depth=6,
    subsample=0.8,
    colsample_bytree=0.8,
    random_state=42
)
model.fit(X_transformed, y_train)



KeyError: 'bike_count'

In [17]:
X_test = utils.get_test_data()

In [19]:
# Merge the DataFrames
merged_conditions = pd.merge(X_test, external_conditions, on='date', how='left')

merged_conditions = utils._column_rename(merged_conditions)
# Ensure "date" is in datetime format
merged_conditions["date"] = pd.to_datetime(merged_conditions["date"], errors="coerce")

# Drop rows with invalid datetime entries
df = merged_conditions.dropna(subset=["date"])

# Extract date and time features
df["year"] = df["date"].dt.year
df["month"] = df["date"].dt.month
df["weekday"] = df["date"].dt.dayofweek
df["day"] = df["date"].dt.day
df["hour"] = df["date"].dt.hour
df["is_weekend"] = (df["weekday"] >= 5).astype(int)

# Handle school and public holidays
unique_dates = df["date"].dt.date.unique()
d = SchoolHolidayDates()
f = JoursFeries()

try:
    dict_school_holidays = {date: d.is_holiday_for_zone(date, "C") for date in unique_dates}
    df["is_school_holiday"] = df["date"].dt.date.map(dict_school_holidays).fillna(0).astype(int)
except Exception as e:
    print(f"Error with school holidays mapping: {e}")
    df["is_school_holiday"] = 0

try:
    dict_public_holidays = {date: f.is_bank_holiday(date, zone="Métropole") for date in unique_dates}
    df["is_public_holiday"] = df["date"].dt.date.map(dict_public_holidays).fillna(0).astype(int)
except Exception as e:
    print(f"Error with public holidays mapping: {e}")
    df["is_public_holiday"] = 0

In [20]:
# Process the test data with the same transformations as the training data
# 1. Apply column transformations
# One-hot encode date columns
date_encoded_test = date_encoder.transform(df[date_cols])

# One-hot encode categorical columns
cat_encoded_test = cat_encoder.transform(df[categorical_cols])

# Standard scale numerical columns
num_scaled_test = num_scaler.transform(df[numerical_cols])

# Combine all transformed features
X_test_transformed_numeric = hstack([date_encoded_test, cat_encoded_test, num_scaled_test]).toarray()

# 2. Make predictions
y_pred = model.predict(X_test_transformed_numeric)


In [21]:
df_submission = pd.DataFrame(y_pred, columns=["log_bike_count"])
df_submission.index.name = "Id"

In [22]:
df_submission.to_csv("/Users/felix/Documents/X/Cours Python/Kaggle/submission/test_pipeline.csv", index=True)